In [ ]:
# from google.colab import drive

# drive.mount("/content/gdrive")

# Setup

In [ ]:
%%capture
!git clone https://github.com/sunzewei2715/Graformer.git
%cd Graformer
!pip install --editable ./
!pip install transformers sacrebleu sentencepiece

!wget "https://docs.google.com/uc?export=download&id=1AvicHuiUzNz5xP66zjLwfdNAKiUrFG4R&confirm=t" -O en-vi.tgz
!mkdir orig
!mv en-vi.tgz orig
!wget "https://docs.google.com/uc?export=download&id=1kqNgpC0N67DdTxIer2k_94hxiS9Vf4rZ&confirm=t" -O prepare-iwslt14-envi.sh

!gdown 1SiLR8bPzXctI-O83lbO9cUd4K4pB3cC7
!gdown 1ms9Dv-UOiLPUjEh3dIS5SYUwV4_eBu9y
!gdown 1OQT4g98ZpKYDQTfY6GFkhMWE1Mxx_qLb
# de
!gdown 10XHzGGBMv_dDezXXDPR8fG6HypiR400y
# en
!gdown 1UbfODsamQGAnPq0s0MLeoWZ2JG4CCoAN

print('Cloning Moses github repository (for tokenization scripts)...')
!git clone https://github.com/moses-smt/mosesdecoder.git

print('Cloning Subword NMT repository (for BPE pre-processing)...')
!git clone https://github.com/rsennrich/subword-nmt.git

# writefile section

In [ ]:
%cd /content/Graformer/fairseq/optim/lr_scheduler

/content/Graformer/fairseq/optim/lr_scheduler


In [ ]:
%%writefile cosine_lr_scheduler.py
# Copyright (c) Facebook, Inc. and its affiliates.
#
# This source code is licensed under the MIT license found in the
# LICENSE file in the root directory of this source tree.

import math
from collections.abc import Collection
from dataclasses import dataclass, field
from typing import List

from omegaconf import II

from fairseq.dataclass import FairseqDataclass
from fairseq.optim.lr_scheduler import FairseqLRScheduler, register_lr_scheduler


@dataclass
class CosineLRScheduleConfig(FairseqDataclass):
    warmup_updates: int = field(
        default=0,
        metadata={"help": "warmup the learning rate linearly for the first N updates"},
    )
    warmup_init_lr: float = field(
        default=-1,
        metadata={
            "help": "initial learning rate during warmup phase; default is cfg.lr"
        },
    )
    lr: List[float] = field(
        default=II("optimization.lr"),
        metadata={"help": "max learning rate, must be more than cfg.min_lr"},
    )
    min_lr: float = field(default=0.0, metadata={"help": "min learning rate"})
    t_mult: float = field(
        default=1.0, metadata={"help": "factor to grow the length of each period"}
    )
    lr_period_updates: float = field(
        default=-1, metadata={"help": "initial number of updates per period"}
    )
    lr_shrink: float = field(
        default=0.1, metadata={"help": "shrink factor for annealing"}
    )
    # This is not required, but is for convenience in inferring lr_period_updates
    max_update: int = II("optimization.max_update")


@register_lr_scheduler("cosine", dataclass=CosineLRScheduleConfig)
class CosineLRSchedule(FairseqLRScheduler):
    """Assign LR based on a cyclical schedule that follows the cosine function.

    See https://arxiv.org/pdf/1608.03983.pdf for details.

    We also support a warmup phase where we linearly increase the learning rate
    from some initial learning rate (``--warmup-init-lr``) until the configured
    max learning rate (``--lr``).

    During warmup::

      lrs = torch.linspace(cfg.warmup_init_lr, cfg.lr, cfg.warmup_updates)
      lr = lrs[update_num]

    After warmup::

      lr = cfg.min_lr + 0.5*(cfg.lr - cfg.min_lr)*(1 + cos(t_curr / t_i))

    where ``t_curr`` is current percentage of updates within the current period
    range and ``t_i`` is the current period range, which is scaled by ``t_mul``
    after every iteration.
    """

    def __init__(self, cfg: CosineLRScheduleConfig, fairseq_optimizer):
        super().__init__(cfg, fairseq_optimizer)
        if isinstance(cfg.lr, Collection) and len(cfg.lr) > 1:
            raise ValueError(
                "Cannot use a fixed learning rate schedule with cosine."
                f" Consider --lr-scheduler=fixed instead. ({cfg.lr})"
            )

        self.max_lr = cfg.lr[0] if isinstance(cfg.lr, Collection) else cfg.lr
        assert (
            self.max_lr > cfg.min_lr
        ), f"max_lr (={cfg.lr}) must be more than min_lr (={cfg.min_lr})"

        warmup_end_lr = self.max_lr
        if cfg.warmup_init_lr < 0:
            cfg.warmup_init_lr = cfg.min_lr

        self.t_mult = cfg.t_mult
        self.period = cfg.lr_period_updates

        if self.period <= 0:
            assert (
                cfg.max_update > 0
            ), "Either --max_update or --lr-period-updates must be set"
            self.period = cfg.max_update - cfg.warmup_updates

        if cfg.warmup_updates > 0:
            # linearly warmup for the first cfg.warmup_updates
            self.lr_step = (warmup_end_lr - cfg.warmup_init_lr) / cfg.warmup_updates
        else:
            self.lr_step = 1

        self.warmup_updates = cfg.warmup_updates
        self.lr_shrink = cfg.lr_shrink

        # initial learning rate
        self.lr = cfg.warmup_init_lr
        self.optimizer.set_lr(self.lr)

    def step(self, epoch, val_loss=None):
        """Update the learning rate at the end of the given epoch."""
        super().step(epoch, val_loss)
        # we don't change the learning rate at epoch boundaries
        return self.optimizer.get_lr()

    def step_update(self, num_updates):
        """Update the learning rate after each update."""
        if num_updates < self.cfg.warmup_updates:
            self.lr = self.cfg.warmup_init_lr + num_updates * self.lr_step
        else:
            curr_updates = num_updates - self.cfg.warmup_updates
            if self.t_mult != 1:
                i = math.floor(
                    math.log(
                        1 - curr_updates / self.period * (1 - self.t_mult), self.t_mult
                    )
                )
                t_i = self.t_mult ** i * self.period
                t_curr = (
                    curr_updates
                    - (1 - self.t_mult ** i) / (1 - self.t_mult) * self.period
                )
            else:
                i = math.floor(curr_updates / self.period)
                t_i = self.period
                t_curr = curr_updates - (self.period * i)

            lr_shrink = self.lr_shrink ** i
            min_lr = self.cfg.min_lr * lr_shrink
            max_lr = self.max_lr * lr_shrink

            self.lr = min_lr + 0.5 * (max_lr - min_lr) * (
                1 + math.cos(math.pi * t_curr / t_i)
            )

        self.optimizer.set_lr(self.lr)
        return self.lr



Overwriting cosine_lr_scheduler.py


In [ ]:
%%writefile inverse_square_root_schedule.py
# Copyright (c) Facebook, Inc. and its affiliates.
#
# This source code is licensed under the MIT license found in the
# LICENSE file in the root directory of this source tree.

from collections.abc import Collection
from dataclasses import dataclass, field
from typing import List

from omegaconf import II

from fairseq.dataclass import FairseqDataclass
from fairseq.optim.lr_scheduler import FairseqLRScheduler, register_lr_scheduler


@dataclass
class InverseSquareRootLRScheduleConfig(FairseqDataclass):
    warmup_updates: int = field(
        default=4000,
        metadata={"help": "warmup the learning rate linearly for the first N updates"},
    )
    warmup_init_lr: float = field(
        default=-1,
        metadata={
            "help": "initial learning rate during warmup phase; default is cfg.lr"
        },
    )
    lr: List[float] = II("optimization.lr")


@register_lr_scheduler("inverse_sqrt", dataclass=InverseSquareRootLRScheduleConfig)
class InverseSquareRootSchedule(FairseqLRScheduler):
    """Decay the LR based on the inverse square root of the update number.

    We also support a warmup phase where we linearly increase the learning rate
    from some initial learning rate (``--warmup-init-lr``) until the configured
    learning rate (``--lr``). Thereafter we decay proportional to the number of
    updates, with a decay factor set to align with the configured learning rate.

    During warmup::

      lrs = torch.linspace(cfg.warmup_init_lr, cfg.lr, cfg.warmup_updates)
      lr = lrs[update_num]

    After warmup::

      decay_factor = cfg.lr * sqrt(cfg.warmup_updates)
      lr = decay_factor / sqrt(update_num)
    """

    def __init__(self, cfg: InverseSquareRootLRScheduleConfig, optimizer):
        super().__init__(cfg, optimizer)
        if isinstance(cfg.lr, Collection) and len(cfg.lr) > 1:
            raise ValueError(
                "Cannot use a fixed learning rate schedule with inverse_sqrt."
                " Consider --lr-scheduler=fixed instead."
            )
        warmup_end_lr = cfg.lr[0] if isinstance(cfg.lr, Collection) else cfg.lr
        if cfg.warmup_init_lr < 0:
            cfg.warmup_init_lr = 0 if cfg.warmup_updates > 0 else warmup_end_lr

        # linearly warmup for the first cfg.warmup_updates
        self.lr_step = (warmup_end_lr - cfg.warmup_init_lr) / cfg.warmup_updates

        # then, decay prop. to the inverse square root of the update number
        self.decay_factor = warmup_end_lr * cfg.warmup_updates ** 0.5

        # initial learning rate
        self.lr = cfg.warmup_init_lr
        self.optimizer.set_lr(self.lr)

    def step(self, epoch, val_loss=None):
        """Update the learning rate at the end of the given epoch."""
        super().step(epoch, val_loss)
        # we don't change the learning rate at epoch boundaries
        return self.optimizer.get_lr()

    def step_update(self, num_updates):
        """Update the learning rate after each update."""
        if num_updates < self.cfg.warmup_updates:
            self.lr = self.cfg.warmup_init_lr + num_updates * self.lr_step
        else:
            self.lr = self.decay_factor * num_updates ** -0.5
        self.optimizer.set_lr(self.lr)
        return self.lr


Overwriting inverse_square_root_schedule.py


In [ ]:
%cd /content/Graformer

/content/Graformer


# Data preparing

In [ ]:
%%writefile prepare-iwslt15-envi.sh
#!/usr/bin/env bash

# Adapted from https://github.com/facebookresearch/MIXER/blob/master/prepareData.sh
SCRIPTS=mosesdecoder/scripts
TOKENIZER=$SCRIPTS/tokenizer/tokenizer.perl
LC=$SCRIPTS/tokenizer/lowercase.perl
CLEAN=$SCRIPTS/training/clean-corpus-n.perl
BPEROOT=subword-nmt/subword_nmt
BPE_TOKENS=10000

#URL="https://wit3.fbk.eu/archive/2014-01/texts/de/en/en-vi.tgz"
GZ=en-vi.tgz
# if [ ! -d "$SCRIPTS" ]; then
#    echo "Please set SCRIPTS variable correctly to point to Moses scripts."
#    exit
# fi

src=en
tgt=vi
lang=en-vi
prep=IWSLT15.tokenized.en-vi
tmp=$prep/tmp
orig=orig

mkdir -p $orig $tmp $prep


#echo "Downloading data from ${URL}..."
cd $orig
#wget "$URL"

#if [ -f $GZ ]; then
 #   echo "Data successfully downloaded."
#else
 #   echo "Data not successfully downloaded."
  #  exit
#fi

tar zxvf $GZ
cd ..

echo "pre-processing train data..."
for l in $src $tgt; do
    f=train.tags.$lang.$l
    tok=train.tags.$lang.tok.$l

    cat $orig/$lang/$f | \
    grep -v '<url>' | \
    grep -v '<talkid>' | \
    grep -v '<keywords>' | \
    sed -e 's/<title>//g' | \
    sed -e 's/<\/title>//g' | \
    sed -e 's/<description>//g' | \
    sed -e 's/<\/description>//g' | \
    perl $TOKENIZER -threads 8 -l $l > $tmp/$tok
    echo ""
done
perl $CLEAN -ratio 1.5 $tmp/train.tags.$lang.tok $src $tgt $tmp/train.tags.$lang.clean 1 175
for l in $src $tgt; do
    perl $LC < $tmp/train.tags.$lang.clean.$l > $tmp/train.tags.$lang.$l
done

echo "pre-processing valid/test data..."
for l in $src $tgt; do
    for o in `ls $orig/$lang/IWSLT15.TED*.$l.xml`; do
    fname=${o##*/}
    f=$tmp/${fname%.*}
    echo $o $f
    grep '<seg id' $o | \
        sed -e 's/<seg id="[0-9]*">\s*//g' | \
        sed -e 's/\s*<\/seg>\s*//g' | \
        sed -e "s/\’/\'/g" | \
    perl $TOKENIZER -threads 8 -l $l | \
    perl $LC > $f
    echo ""
    done
done


echo "creating train, valid, test..."
for l in $src $tgt; do
    awk '{if (NR%23 == 0)  print $0; }' $tmp/train.tags.en-vi.$l > $tmp/valid.$l
    awk '{if (NR%23 != 0)  print $0; }' $tmp/train.tags.en-vi.$l > $tmp/train.$l

    cat $tmp/IWSLT15.TED.dev2010.en-vi.$l \
        $tmp/IWSLT15.TED.tst2013.en-vi.$l \
        $tmp/IWSLT15.TED.tst2010.en-vi.$l \
        $tmp/IWSLT15.TED.tst2011.en-vi.$l \
        $tmp/IWSLT15.TED.tst2012.en-vi.$l \
        > $tmp/test.$l
done

TRAIN=$tmp/train.en-vi
BPE_CODE=$prep/code
rm -f $TRAIN
for l in $src $tgt; do
    cat $tmp/train.$l >> $TRAIN
done

echo "encoding train with learned BPE..."
tmp=/content/Graformer/IWSLT15.tokenized.en-vi/tmp
python /content/Graformer/scripts/spm_encode.py \
    --model "/content/Graformer/sentencepiece.model" \
    --output_format=piece \
    --inputs $tmp/train.vi $tmp/train.en \
    --outputs $tmp/train.bpe.vi $tmp/train.bpe.en

echo "encoding test with learned BPE..."
tmp=/content/Graformer/IWSLT15.tokenized.en-vi/tmp
python /content/Graformer/scripts/spm_encode.py \
    --model "/content/Graformer/sentencepiece.model" \
    --output_format=piece \
    --inputs $tmp/test.vi $tmp/test.en \
    --outputs $tmp/test.bpe.vi $tmp/test.bpe.en

echo "encoding valid with learned BPE..."
tmp=/content/Graformer/IWSLT15.tokenized.en-vi/tmp
python /content/Graformer/scripts/spm_encode.py \
    --model "/content/Graformer/sentencepiece.model" \
    --output_format=piece \
    --inputs $tmp/valid.vi $tmp/valid.en \
    --outputs $tmp/valid.bpe.vi $tmp/valid.bpe.en


Writing prepare-iwslt15-envi.sh


In [ ]:
!bash prepare-iwslt15-envi.sh

en-vi/
en-vi/IWSLT15.TED.dev2010.en-vi.en.xml
en-vi/IWSLT15.TED.dev2010.en-vi.vi.xml
en-vi/IWSLT15.TED.tst2010.en-vi.en.xml
en-vi/IWSLT15.TED.tst2010.en-vi.vi.xml
en-vi/IWSLT15.TED.tst2011.en-vi.en.xml
en-vi/IWSLT15.TED.tst2011.en-vi.vi.xml
en-vi/IWSLT15.TED.tst2012.en-vi.en.xml
en-vi/IWSLT15.TED.tst2012.en-vi.vi.xml
en-vi/IWSLT15.TED.tst2013.en-vi.en.xml
en-vi/IWSLT15.TED.tst2013.en-vi.vi.xml
en-vi/README
en-vi/train.tags.en-vi.en
en-vi/train.tags.en-vi.vi
en-vi/train.vi
pre-processing train data...
Tokenizer Version 1.1
Language: en
Number of threads: 8

Tokenizer Version 1.1
Language: vi
Number of threads: 8

clean-corpus.perl: processing IWSLT15.tokenized.en-vi/tmp/train.tags.en-vi.tok.en & .vi to IWSLT15.tokenized.en-vi/tmp/train.tags.en-vi.clean, cutoff 1-175, ratio 1.5
..........(100000)...
Input sentences: 136891  Output sentences:  117055
pre-processing valid/test data...
orig/en-vi/IWSLT15.TED.dev2010.en-vi.en.xml IWSLT15.tokenized.en-vi/tmp/IWSLT15.TED.dev2010.en-vi.en
Token

In [ ]:
# Binarize the de-en dataset
%env TEXT=/content/Graformer/IWSLT15.tokenized.en-vi/tmp
!fairseq-preprocess --source-lang en --target-lang vi \
    --trainpref $TEXT/train.bpe \
    --validpref $TEXT/valid.bpe \
    --testpref $TEXT/test.bpe \
    --destdir data-bin/iwslt15.tokenized.en-vi \
    --workers 20 \
    --joined-dictionary --tgtdict /content/Graformer/sentencepiece_refine.vocab

env: TEXT=/content/Graformer/IWSLT15.tokenized.en-vi/tmp
2023-06-09 01:36:29.939511: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-06-09 01:36:31.269376: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
2023-06-09 01:36:35 | INFO | fairseq_cli.preprocess | Namespace(no_progress_bar=False, log_interval=100, log_format=None, tensorboard_logdir=None, wandb_project=None, azureml_logging=False, seed=1, cpu=False, tpu=False, bf16=False, memory_efficient_bf16=False, fp16=False, memory_efficient_fp16=False, fp16_no_flatten_grads=False, fp16_init_scale=128, fp16_scale_window=None, fp16_scale_tolerance=0.0, min_loss_scale=0.0001, threshold_loss_scale=None, user_dir=None, empty_cache_freq=0, all_gather_l

In [ ]:
# import shutil

# shutil.rmtree("/content/Graformer/data-bin")

# Train the model

In [ ]:
!gdown 1FiL620wn2GL_TxD4tkj2PvUrEnuVBWX0

Downloading...
From: https://drive.google.com/uc?id=1FiL620wn2GL_TxD4tkj2PvUrEnuVBWX0
To: /content/Graformer/graformer.pt
100% 5.44G/5.44G [00:49<00:00, 110MB/s]


In [ ]:
!python train.py --num-workers 8 \
    data-bin/iwslt15.tokenized.en-vi \
    --arch bridge_transformer \
    --task translation_from_pretrained_model \
    --arch bridge_transformer \
    --encoder-layers 12 --decoder-layers 12 \
    --no-encoder-attn-layers 0,1,2,3,4,5 \
    --encoder-learned-pos --decoder-learned-pos \
    --no-scale-embedding \
    --encoder-normalize-before --decoder-normalize-before \
    --activation-fn gelu \
    --finetune-from-model /content/Graformer/graformer.pt \
    --freeze-params "(.embed.)|(.layers\.(0|1|2|3|4|5)\..)|(.layers\.6\.self_attn_layer_norm.)" \
    --transfer-params "encoder.layer_norm.weight:encoder.layers.6.self_attn_layer_norm.weight,decoder.layer_norm.weight:decoder.layers.6.self_attn_layer_norm.weight,encoder.layer_norm.bias:encoder.layers.6.self_attn_layer_norm.bias,decoder.layer_norm.bias:decoder.layers.6.self_attn_layer_norm.bias,decoder.embed_tokens.weight:decoder.lm_output_projection.weight,decoder.layer_norm.weight:decoder.lm_layer_norm.weight,decoder.layer_norm.bias:decoder.lm_layer_norm.bias" \
    --lm-fusion \
    --max-update 100000000 \
    --max-tokens 4000 \
    --optimizer adam --adam-betas '(0.9,0.98)' \
    --lr 0.001 --warmup-init-lr '1e-07' --min-loss-scale 0.0 \
    --lr-scheduler inverse_sqrt \
    --warmup-updates 4000 \
    --update-freq 5  \
    --criterion label_smoothed_cross_entropy --label-smoothing 0.1 \
    --dropout 0.1 \
    --no-epoch-checkpoints \
    --save-dir /content/gdrive/MyDrive/Graformer \
    --ddp-backend=no_c10d $(echo ${extra_args[@]})
    # --fp16 \

2023-05-05 07:41:13.259292: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-05-05 07:41:14.384053: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
2023-05-05 07:41:20 | INFO | fairseq_cli.train | {'_name': None, 'common': {'_name': None, 'no_progress_bar': False, 'log_interval': 100, 'log_format': None, 'tensorboard_logdir': None, 'wandb_project': None, 'azureml_logging': False, 'seed': 1, 'cpu': False, 'tpu': False, 'bf16': False, 'memory_efficient_bf16': False, 'fp16': False, 'memory_efficient_fp16': False, 'fp16_no_flatten_grads': False, 'fp16_init_scale': 128, 'fp16_scale_window': None, 'fp16_scale_tolerance': 0.0, 'min_loss_scale': 0.0, 'threshold_loss_scale': None, 'user_dir': None, 'empty_cache_

# Test the model

In [ ]:
!gdown 10sm1iSjPEsTz-YDS4fh-FFHALYBupDRy

Downloading...
From: https://drive.google.com/uc?id=10sm1iSjPEsTz-YDS4fh-FFHALYBupDRy
To: /content/Graformer/checkpoint_best.pt
100% 4.30G/4.30G [00:35<00:00, 122MB/s]


In [ ]:
!fairseq-generate /content/Graformer/data-bin/iwslt15.tokenized.en-vi \
    --path /content/Graformer/checkpoint_best.pt \
    --batch-size 32 --beam 5 \
    --remove-bpe sentencepiece

Streaming output truncated to the last 5000 lines.
D-5599	-0.35473212599754333	bạn có thể google , nhưng đó là một nhiễm trùng , không phải là cơ hội , mà là đường không khí trên , và nó thực sự có thể làm cho đường không kết thúc đóng kết thúc .
P-5599	-2.7575 -0.3801 -0.0064 -0.0415 -0.0202 -0.0131 -0.0330 -0.2139 -0.0112 -1.0089 -0.2887 -0.1292 -0.0116 -0.0086 -0.0141 -0.6956 -0.0047 -0.0800 -0.1222 -0.4280 -0.0363 -0.0055 -3.4406 -0.2343 -0.4238 -0.0270 -0.8886 -0.0185 -0.1117 -0.0389 -0.5616 -0.1769 -0.0115 -0.0051 -0.0067 -0.0073 -0.2802 -0.0252 -0.0200 -0.4473 -1.1767 -1.7396 -0.6349 -1.4631 -1.0893 -0.2848 -0.4672 -0.0081 -0.4745 -1.4241 -0.0106 -0.0399 -0.0362 -0.0032 -0.0070 -0.4776 -0.0095 -0.0060 -0.0092 -0.0078 -0.7950 -0.0258 -0.0452 -0.5076 -0.1628 -1.2453 -0.1899 -0.0094 -0.5871 -0.0396 -1.0770 -0.4893 -0.0067 -0.1320 -0.0419 -0.8652 -0.0869 -0.0261 -0.0275 -0.5507 -0.0647 -0.3243 -1.2202 -0.0013 -0.0848 -0.0472 -0.0043 -0.0107 -0.4507 -0.0182 -0.0295 -0.0106 -0.0130 -0

In [ ]:
!fairseq-generate /content/Graformer/data-bin/iwslt15.tokenized.en-vi \
    --path /content/Graformer/checkpoint_best.pt \
    --batch-size 32 --beam 5 \
    --remove-bpe

Streaming output truncated to the last 5000 lines.
D-5599	-0.35473212599754333	▁b ạ n ▁c ó ▁th ể ▁go ogle ▁, ▁n h ư n g ▁ đ ó ▁là ▁m ộ t ▁n hi ễ m ▁tr ù n g ▁, ▁k h ô n g ▁ph ả i ▁là ▁c ơ ▁h ộ i ▁, ▁m à ▁là ▁ đ ư ờ n g ▁k h ô n g ▁k h í ▁tr ên ▁, ▁v à ▁n ó ▁th ự c ▁s ự ▁c ó ▁th ể ▁là m ▁cho ▁ đ ư ờ n g ▁k h ô n g ▁k ế t ▁th ú c ▁ đ ón g ▁k ế t ▁th ú c ▁.
P-5599	-2.7575 -0.3801 -0.0064 -0.0415 -0.0202 -0.0131 -0.0330 -0.2139 -0.0112 -1.0089 -0.2887 -0.1292 -0.0116 -0.0086 -0.0141 -0.6956 -0.0047 -0.0800 -0.1222 -0.4280 -0.0363 -0.0055 -3.4406 -0.2343 -0.4238 -0.0270 -0.8886 -0.0185 -0.1117 -0.0389 -0.5616 -0.1769 -0.0115 -0.0051 -0.0067 -0.0073 -0.2802 -0.0252 -0.0200 -0.4473 -1.1767 -1.7396 -0.6349 -1.4631 -1.0893 -0.2848 -0.4672 -0.0081 -0.4745 -1.4241 -0.0106 -0.0399 -0.0362 -0.0032 -0.0070 -0.4776 -0.0095 -0.0060 -0.0092 -0.0078 -0.7950 -0.0258 -0.0452 -0.5076 -0.1628 -1.2453 -0.1899 -0.0094 -0.5871 -0.0396 -1.0770 -0.4893 -0.0067 -0.1320 -0.0419 -0.8652 -0.0869 -0.0261 -0.0275 -0.5